Coronavirus Coverage by US State
================================

A quick investigation into media coverage of the coronavirus pandemic by state in the US.
By Rahul Bhargava

## Setup

In [ ]:
# Install the requirements
import sys
!{sys.executable} -m pip install -r requirements.txt

In [1]:
from IPython.display import JSON
import numpy as np
import os, mediacloud.api
import csv
import datetime as dt
from bokeh.io import export_svgs
import pandas as pd
from bokeh.io import output_notebook
from bokeh.plotting import figure, show
from bokeh.models import ColumnDataSource
from bokeh.palettes import Spectral3
from bokeh.layouts import gridplot
from bokeh.models import NumeralTickFormatter
from dotenv import load_dotenv
import json
load_dotenv()  # load config from .env file
output_notebook()

Loading BokehJS ...

In [56]:
mc = mediacloud.api.MediaCloud(os.getenv('MC_API_KEY'))
mediacloud.__version__
COVID_QUERY = 'coronavirus OR covid OR "covid 19" OR "covid-19" OR covid19 OR pandemic'
START_DATE = dt.date(2020,2,1)
END_DATE = dt.date(2021,12,1)
DATE_RANGE = mc.dates_as_query_clause(START_DATE, END_DATE)
US_TOP_2018_COLLECTION = 186572516
DATA_FILE = os.path.join('data', 'state-media-data.json')

## Assess High Level national coverage

In [57]:
national_covid_attention = mc.storyCount("({}) AND tags_id_media:{}".format(COVID_QUERY, US_TOP_2018_COLLECTION), DATE_RANGE, split=True)
national_attention = mc.storyCount("tags_id_media:{}".format(US_TOP_2018_COLLECTION), DATE_RANGE, split=True)
national_data = []
for day in national_attention['counts']:
    date = day['date']
    total_stories = day['count']
    covid_day = [d for d in national_covid_attention['counts'] if d['date']==date]
    covid_stories = covid_day[0]['count'] if len(covid_day) == 1 else 0
    national_data.append({'date': date, 'total': total_stories, 'covid': covid_stories})
national_df = pd.DataFrame(national_data)
national_df['date'] = pd.to_datetime(national_df['date'], format='%Y-%m-%d')
national_df = national_df.sort_values(by='date')
national_df['pct'] = national_df['covid'] / national_df['total']
national_df['rolling_pct'] = national_df.rolling(window=3)['pct'].mean()
national_df.to_csv(os.path.join('data','national-attention.csv'))
national_df.head()

date  total  covid       pct  rolling_pct
0 2020-02-01   2384    204  0.085570          NaN
1 2020-02-02   2400    206  0.085833          NaN
2 2020-02-03   3395    381  0.112224     0.094543
3 2020-02-04   3757    428  0.113921     0.103993
4 2020-02-05   3820    413  0.108115     0.111420

In [59]:
# chart overall national attention
p = figure(plot_width=1400, plot_height=600, x_axis_type='datetime', title="Coronavirus National Coverage", y_range=(0, 1))
p.line(x='date', y='rolling_pct', line_width=1, source=ColumnDataSource(national_df), line_color='teal')
p.yaxis.formatter = NumeralTickFormatter(format='0 %')
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
#p.axis.visible = False
p.outline_line_color = None
p.toolbar.logo = None
p.toolbar_location = None
p.output_backend = "svg"
#export_svgs(p, filename="images/attention - top online.svg")
show(p)

## Grab Coronavirus attention by state from Media Cloud

### 1. Generate Static List of US Media by State (run just once)

In [ ]:
# load all US state tags (static file coped from MediaCloud-Web-tools repository)
geo_tag_hierarchy = json.load(open(os.path.join('data','mc-geo-adm1.json')))['byCountry']
us = [country for country in geo_tag_hierarchy if country['country']['alpha3'] == 'USA'][0]
# filter out the "national" and combined "state & local" collections
us_state_collections = [s for s in us['collections'] if not s['label'].startswith('United States')]
# add in a handy state name
for s in us_state_collections:
    s['name'] = s['label'].split(',')[0]
us_state_collections[0]

In [ ]:
# now get the media in each collection
def all_media_list(**kwargs):
    # page through a list of media list results (copied from Media Cloud API Tutorial notebooks)
    last_media_id = None
    more_results = True
    matching_media = []
    while more_results:
        media_page = mc.mediaList(**kwargs, last_media_id=last_media_id)
        #print("  got a page of {} matching media".format(len(media_page)))
        if len(media_page) == 0:
            more_results = False
        else:
            matching_media += media_page
            last_media_id = media_page[-1]['media_id']
    return matching_media

pr_collection = mc.tag(34412297)
pr_collection['name'] = "Puerto Rico"
pr_collection['tag'] = "geo_US-PR"
us_state_collections.append(pr_collection)

for s in us_state_collections:
    state_media = all_media_list(tags_id=s['tags_id'], rows=500)
    s['media'] = state_media
    s['media_count'] = len(state_media)
    s['avg_stories_per_day'] = round(sum([m['num_stories_90'] for m in state_media]))
    print("{} - {} media sources ({} stories/day)".format(s['name'], len(s['media']), s['avg_stories_per_day']))

In [ ]:
# cache state collections locally in a file so we don't hit the server over and over
with open(DATA_FILE, 'w') as outfile:
    json.dump(us_state_collections, outfile)

### 2. Add in State Coronavirus Attention Data (run just once)

In [60]:
# load the static file of media sources by state, which now includes media lists for each state
us_state_collections = json.load(open(DATA_FILE))
len(us_state_collections)

52

In [61]:
def state_data_worker(job):
    results = job.copy()
    # add in the total number of stories published from sources in this state
    results['total_stories'] = mc.storyCount("tags_id_media:{}".format(job['tags_id']), DATE_RANGE, split=True)['counts']
    # add in the total number of stories ABOUT COVID published from sources in this state
    results['covid_stories'] = mc.storyCount("tags_id_media:{} AND {}".format(job['tags_id'], COVID_QUERY), DATE_RANGE, split=True)['counts']
    return results

import multiprocess as mp
pool = mp.Pool(16)
us_state_collections = pool.map(state_data_worker, us_state_collections)

In [62]:
# generate CSVs of attention data for each state
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    state_csv_file = os.path.join('data', 'state-attention', "{}-stories.csv".format(state_abbr))
    s['state_csv_file'] = state_csv_file
    data = []
    for day in s['total_stories']:
        date = day['date']
        total_stories = day['count']
        covid_day = [d for d in s['covid_stories'] if d['date']==date] # if there were no stories, day won't have entry in covid results
        covid_stories = covid_day[0]['count'] if len(covid_day) == 1 else 0
        data.append({'state': s['name'],
                     'date': date,
                     'total': total_stories,
                     'covid': covid_stories
                    })
    with open(state_csv_file, 'w') as csvfile:
        writer = csv.DictWriter(csvfile, fieldnames=['state', 'date', 'total', 'covid'], extrasaction='ignore')
        writer.writeheader()
        for d in data:
            writer.writerow(d)
# and add the CSV path to the main file
with open(DATA_FILE, 'w') as outfile:
    json.dump(us_state_collections, outfile)

### 3. Chart Attention Data

In [63]:
order = ['AK', None, None, None, None, None, None, None, None, 'VT', 'NH', 'ME',
        None, None, None, None, None, None, None, None, 'NY', 'CT', 'MA', None,
        'WA', 'MT', 'ND', 'SD', 'MN', 'WI', 'MI', None, 'PA', 'NJ', 'RI', None,
        'OR', 'ID', 'WY', 'NE', 'IA', 'IL', 'IN', 'OH', 'VA', 'DC', 'DE', None,
        'NV', 'UT', 'CO', 'KS', 'MO', 'TN', 'KY', 'WV', 'NC', 'MD', None, None,
        'CA', 'AZ', 'NM', 'OK', 'AR', 'MS', 'AL', 'GA', 'SC', None, None, None,
        None, None, None, 'TX', 'LA', None, None, None, 'FL', None, None, None,
        'HI', None, None, None, None, None, None, None, None, None, None, 'PR',]
def chunks(lst, n):
    #https://stackoverflow.com/questions/312443/how-do-you-split-a-list-into-evenly-sized-chunks
    for i in range(0, len(lst), n):
        yield lst[i:i + n]

In [64]:
# load the static file of media sources by state, which now also has attention data
us_state_collections = json.load(open(DATA_FILE))
total_stories = sum([d['count'] for s in us_state_collections for d in s['total_stories']])
covid_stories = sum([d['count'] for s in us_state_collections for d in s['covid_stories']])
"{:.2%} of stories are about corona ({:,} / {:,})".format((covid_stories/total_stories), covid_stories, total_stories)

'16.55% of stories are about corona (7,625,690 / 46,067,693)'

In [65]:
# make a dataset for each state
media_state_df = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    state_df = pd.read_csv(os.path.join('data','state-attention','{}-stories.csv'.format(state_abbr)))
    state_df['date'] = pd.to_datetime(state_df['date'], format='%Y-%m-%d')
    state_df = state_df.sort_values(by='date')
    state_df['pct'] = state_df['covid'] / state_df['total']
    state_df['rolling_pct'] = state_df.rolling(window=3)['pct'].mean()
    state_df.dropna()
    media_state_df[state_abbr] = state_df
media_state_df['MA'].head()
df.to_csv('data/state-level-attention.csv')

In [66]:
# make a combined chart of all states
# make a chart for each state
media_plots_by_abbr = {}
p = figure(plot_width=1400, plot_height=600, x_axis_type='datetime', title="Coronavirus Coverage by State", y_range=(0, 1))
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    df = media_state_df[state_abbr]
    source = ColumnDataSource(df)
    p.line(x='date', y='rolling_pct', line_width=1, source=source, line_color='teal')
p.yaxis.formatter = NumeralTickFormatter(format='0 %')
p.xgrid.grid_line_color = None
p.ygrid.grid_line_color = None
#p.axis.visible = False
p.outline_line_color = None
p.toolbar.logo = None
p.toolbar_location = None
p.output_backend = "svg"
#export_svgs(p, filename="images/attention - state overlay.svg")
show(p)

In [17]:
# make a chart for each state
media_plots_by_abbr = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    df = media_state_df[state_abbr]
    # now make a chart for the state
    source = ColumnDataSource(df)
    p = figure(plot_width=140, plot_height=140, x_axis_type='datetime', title=s['name'], title_location="below", y_range=(0, 1))
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.axis.visible = False
    p.outline_line_color = None
    p.toolbar.logo = None
    p.toolbar_location = None
    p.line(x='date', y='rolling_pct', line_width=1, source=source, line_color='teal')
    media_plots_by_abbr[state_abbr] = p
    #show(p)
# now let's replicate R's geofacet library by hand
geo_aligned_media_plots = []
for abbr in order:
    plot = media_plots_by_abbr[abbr] if abbr is not None else None
    geo_aligned_media_plots.append(plot)
rows = list(chunks(geo_aligned_media_plots,12))
grid = gridplot(rows)
show(grid)

## Grab Coronavirus incidence/death data from John Hopkins

Attribute the data as the "COVID-19 Data Repository by the Center for Systems Science and Engineering (CSSE) at Johns Hopkins University" or "JHU CSSE COVID-19 Data" for short, and the url: https://github.com/CSSEGISandData/COVID-19.

In [67]:
# download the latest data from their repository on GitHub
# https://github.com/CSSEGISandData/COVID-19
import wget, zipfile
JH_GH_REPO_URL = "https://github.com/CSSEGISandData/COVID-19/archive/refs/heads/master.zip"
dest_path = os.path.join('tmp/jh-repo.zip')
wget.download(JH_GH_REPO_URL, dest_path)
with zipfile.ZipFile(dest_path, 'r') as zip_ref:
    zip_ref.extractall('tmp')

100% [......................................................................] 277027625 / 277027625

In [68]:
# aggregate the covid data by state so we can chart it
import pathlib, dateparser
state_data_path = os.path.join('tmp', 'COVID-19-master', 'csse_covid_19_data', 'csse_covid_19_daily_reports_us') # this folder has one CSV per day and one row per state
state_csv_files = [os.path.join(state_data_path, f) for f in os.listdir(state_data_path) if f.endswith('.csv')]
print("Found {} daily files".format(len(state_csv_files)))
state_name2abbr = {t['name']:t['tag'][-2:] for t in us_state_collections}
state_data = []
for data_file in state_csv_files:
    state_covid_df = pd.read_csv(data_file)
    for index, row in state_covid_df.iterrows():
        if row['Province_State'] in state_name2abbr:
            item = {
                'state': state_name2abbr[row['Province_State']],
                'date': dateparser.parse(pathlib.PurePath(data_file).name[:-3]),
                'cases': row['Confirmed'],
                'deaths': row['Deaths'],
                'incidence': row['Incident_Rate'],
            }
            state_data.append(item)
# write combined CSV of state-level data by day
with open(os.path.join('data','covid-by-state.csv'), 'w') as fd:
    csv_writer = csv.DictWriter(fd, ['state', 'date', 'cases', 'deaths', 'incidence'])
    csv_writer.writeheader()
    csv_writer.writerows(state_data) 
print("Wrote {} daily state records".format(len(state_data)))

Found 598 daily files


/Users/rahulb/.pyenv/versions/3.9.6/envs/jupyterlab/lib/python3.9/site-packages/dateparser/date_parser.py:35: PytzUsageWarning: The localize method is no longer necessary, as this time zone supports the fold attribute (PEP 495). For more details on migrating to a PEP 495-compliant implementation, see https://pytz-deprecation-shim.readthedocs.io/en/latest/migration.html
  date_obj = stz.localize(date_obj)


Wrote 31096 daily state records


In [83]:
data_cols = ['cases', 'deaths', 'incidence']

# cleanup and average a little
jh_df = pd.read_csv(os.path.join('data','covid-by-state.csv'))
jh_df['date'] = pd.to_datetime(jh_df['date'], format='%Y-%m-%d')
valid_range = (jh_df['date'] > START_DATE.strftime("%Y-%m-%d")) & (jh_df['date'] <= END_DATE.strftime("%Y-%m-%d"))
jh_df = jh_df.loc[valid_range]
# apply a window to smooth out weekends and show more of a trend chart (ie. not as spikey)
jh_df['cases'] = pd.to_numeric(jh_df['cases'])
jh_df['deaths'] = pd.to_numeric(jh_df['deaths'])
jh_df['incidence'] = pd.to_numeric(jh_df['incidence'])
jh_df = jh_df.dropna()
print("{} total days".format(len(jh_df['date'].unique())))

598 total days


In [86]:
# make a dataset for each state
rolling_avg_window_size = 7
covid_state_df = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    state_df = jh_df[jh_df['state'] == state_abbr]
    state_df = state_df.sort_values(by='date')
    # the columns are are cumulatve, so do a shift and subtract to get new-per-day
    state_df[data_cols] -= state_df[data_cols].shift(1).fillna(0)
    state_df = state_df[1:] # dump the first day because after the shift/subtract it isn't valid
    state_df['rolling_incidence'] = state_df.rolling(window=rolling_avg_window_size)['incidence'].mean()
    state_df['rolling_cases'] = state_df.rolling(window=rolling_avg_window_size)['cases'].mean()
    state_df['rolling_deaths'] = state_df.rolling(window=rolling_avg_window_size)['deaths'].mean()
    state_df.dropna()
    state_df.to_csv(os.path.join('data','state-covid','covid-by-state-{}.csv'.format(state_abbr)))
    covid_state_df[state_abbr] = state_df
covid_state_df['MA'].head()

state       date   cases  deaths  incidence  rolling_incidence  \
10577    MA 2020-04-13  1392.0    88.0  20.280394                NaN   
6365     MA 2020-04-14  1297.0     0.0  18.896315                NaN   
6313     MA 2020-04-15  1754.0   264.0  25.554462                NaN   
16869    MA 2020-04-16  2263.0     0.0  32.970209                NaN   
16921    MA 2020-04-17  2221.0   137.0  32.358301                NaN   

       rolling_cases  rolling_deaths  
10577            NaN             NaN  
6365             NaN             NaN  
6313             NaN             NaN  
16869            NaN             NaN  
16921            NaN             NaN

In [88]:
# now build each data set into a plot by state
show_cases = False # defaults to incidence
covid_plots_by_abbr = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    state_df = covid_state_df[state_abbr]
    # now make a chart for the state
    source = ColumnDataSource(state_df)
    if show_cases:
        p = figure(plot_width=140, plot_height=140, x_axis_type='datetime', title=s['name'], title_location="below", y_range=(0, 20000))
        p.line(x='date', y='rolling_cases', line_width=1, source=source, line_color='purple')
    else:
        p = figure(plot_width=140, plot_height=140, x_axis_type='datetime', title=s['name'], title_location="below", y_range=(0, 200))
        p.line(x='date', y='rolling_incidence', line_width=1, source=source, line_color='purple')
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.axis.visible = False
    p.outline_line_color = None
    p.toolbar.logo = None
    p.toolbar_location = None
    covid_plots_by_abbr[state_abbr] = p
    #show(p)
# now let's replicate R's geofacet library by hand
covid_geo_aligned_plots = []
for abbr in order:
    plot = covid_plots_by_abbr[abbr] if abbr is not None else None
    covid_geo_aligned_plots.append(plot)
rows = list(chunks(covid_geo_aligned_plots,12))
grid = gridplot(rows)
show(grid)

## Compare incidence rate and media coverage for each state

In [89]:
# pull together the two datesets, by state/day
merged_state_df = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    media_df = media_state_df[state_abbr]
    covid_df = covid_state_df[state_abbr]
    merged_state_df[state_abbr] = pd.merge(media_df, covid_df, left_on='date', right_on='date')
merged_state_df['MA'].head()

state_x       date  total  covid       pct  rolling_pct state_y  \
0  Massachusetts 2020-04-13   2700   1741  0.644815     0.667689      MA   
1  Massachusetts 2020-04-14   2804   1643  0.585949     0.634732      MA   
2  Massachusetts 2020-04-15   3269   1755  0.536861     0.589208      MA   
3  Massachusetts 2020-04-16   3303   1858  0.562519     0.561776      MA   
4  Massachusetts 2020-04-17   2594   1364  0.525829     0.541736      MA   

    cases  deaths  incidence  rolling_incidence  rolling_cases  rolling_deaths  
0  1392.0    88.0  20.280394                NaN            NaN             NaN  
1  1297.0     0.0  18.896315                NaN            NaN             NaN  
2  1754.0   264.0  25.554462                NaN            NaN             NaN  
3  2263.0     0.0  32.970209                NaN            NaN             NaN  
4  2221.0   137.0  32.358301                NaN            NaN             NaN

In [90]:
from bokeh.plotting import figure, output_file, show
from bokeh.models import LinearAxis, Range1d
merged_state_plots = {}
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    df = merged_state_df[state_abbr]
    p = figure(plot_width=140, plot_height=140, x_axis_type='datetime', title=s['name'], title_location="below")
    # add media coverage pct
    p.line(df['date'], df['rolling_pct'], line_width=1, color="teal")
    p.y_range = Range1d(0,1)
    # add covid incidence rate (per 100,000)
    p.extra_y_ranges = { 'incidence_range': Range1d(start=0, end=200)}
    p.add_layout(LinearAxis(y_range_name='incidence_range'), "right")
    p.line(df['date'], df['rolling_incidence'], line_width=1, y_range_name='incidence_range', color='purple')
    # clean up for display
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.axis.visible = False
    p.outline_line_color = None
    p.toolbar.logo = None
    p.toolbar_location = None
    merged_state_plots[state_abbr] = p
#show(p)
# now let's replicate R's geofacet library by hand
merged_geo_aligned_plots = []
for abbr in order:
    plot = merged_state_plots[abbr] if abbr is not None else None
    merged_geo_aligned_plots.append(plot)
rows = list(chunks(merged_geo_aligned_plots,12))
grid = gridplot(rows)
show(grid)

In [91]:
# dig into certain states
spotlight_state_collections = [s for s in us_state_collections if s['tag'].split('-')[1] in ['MA', 'AZ']]
plots = []
for s in spotlight_state_collections:
    state_abbr = s['tag'].split('-')[1]
    df = merged_state_df[state_abbr]
    p = figure(plot_width=500, plot_height=500, x_axis_type='datetime', title=s['name'], title_location="below")
    # add media coverage pct
    p.line(df['date'], df['rolling_pct'], line_width=2, color="teal") #, legend_label="stories")
    p.y_range = Range1d(0,1)
    # add covid incidence rate (per 100,000)
    p.extra_y_ranges = { 'incidence_range': Range1d(start=0, end=200)}
    p.add_layout(LinearAxis(y_range_name='incidence_range'), "right")
    p.line(df['date'], df['rolling_incidence'], line_width=2, y_range_name='incidence_range', color='purple') #legend_label="incidence per 100,000")
    # clean up for display
    p.xgrid.grid_line_color = None
    p.ygrid.grid_line_color = None
    p.yaxis.visible = False
    p.outline_line_color = None
    p.toolbar.logo = None
    p.toolbar_location = None
    #p.legend.location = "top_right"
    #p.legend.click_policy="hide"
    p.output_backend = "svg"
    #export_svgs(p, filename="images/comparison - {}.svg".format(state_abbr))
    plots.append(p)
grid = gridplot([plots])
show(grid)

## Hypothesis - is this caused by Associated Press Stories?

In [ ]:
SAMPLE_SIZE = 1000
# save random stories from each collection
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    random_state_stories = mc.storyList("tags_id_media:{} AND {}".format(s['tags_id'], COVID_QUERY), DATE_RANGE, sort=mc.SORT_RANDOM, rows=SAMPLE_SIZE)
    story_df = pd.DataFrame(random_state_stories)
    story_df.to_csv(os.path.join('data', 'state-sample-stories', 'sample-stories-{}.csv'.format(state_abbr)))

In [ ]:
# check the already-saved random stories from each state collection to if they mention "associated press" in their text
results = []
for s in us_state_collections:
    state_abbr = s['tag'].split('-')[1]
    random_state_stories = pd.read_csv(os.path.join('data', 'state-sample-stories', 'sample-stories-{}.csv'.format(state_abbr)))
    guessed_as_ap_stories = random_state_stories[random_state_stories['ap_syndicated']==True].shape[0]
    data = { 'state': state_abbr, 'ap_syndicated_pct': guessed_as_ap_stories / SAMPLE_SIZE }
    results.append(data)

In [ ]:
story_ap_df = pd.DataFrame(results)
story_ap_df.head()
story_ap_df.to_csv(os.path.join("data","state-ap-stories.csv"))

In [ ]:
# https://towardsdatascience.com/interactive-histograms-with-bokeh-202b522265f3
def hist_hover(dataframe, column, colors=["SteelBlue", "Tan"], bins=30, show_plot=True):
    # build histogram data with Numpy
    hist, edges = np.histogram(dataframe[column], bins = bins)
    hist_df = pd.DataFrame({column: hist,
                             "left": edges[:-1],
                             "right": edges[1:]})
    hist_df["interval"] = ["%d to %d" % (left, right) for left, 
                           right in zip(hist_df["left"], hist_df["right"])]
    # bokeh histogram with hover tool
    src = ColumnDataSource(hist_df)
    plot = figure(plot_height = 600, plot_width = 600,
          title = "Histogram of {}".format(column.capitalize()),
          x_axis_label = "pct AP syndicated stories in sample",
          y_axis_label = "count of states")
    plot.xaxis.formatter = NumeralTickFormatter(format='0 %')
    plot.quad(bottom = 0, top = column,left = "left", 
        right = "right", source = src, fill_color = colors[0], 
        line_color = "black", fill_alpha = 0.7,
        hover_fill_alpha = 1.0, hover_fill_color = colors[1])
    # output
    if show_plot == True:
        show(plot)
    else:
        return plot
    
hist_hover(story_ap_df, 'ap_syndicated_pct', bins=10)